# Note to Reviewers

This code cannot be executed directly for several reasons:

1. It requires users to provide their own API tokens for paid large language models (LLMs).
2. The similarity functionality has been implemented as an API in our system, it will be released to the whole community in camera-ready.
3. The PathBuilder (PB) codebase is complex, and only key functions are presented here.

The purpose of sharing this code is to allow reviewers to examine our critical work, including data generation processes, the PathBuilder implementation, and our fully automated benchmark evaluation system for LLMs. This preview provides insight into our methodological approach while acknowledging the practical limitations of direct execution.

In [1]:
import os
print(os.getcwd())
import sklearn
import traceback
import time
import openai
from openai import OpenAI
openai.api_key = ""
print(openai.__version__)
from dotenv import load_dotenv
load_dotenv()  



f:\Github\EMNLP2025_Turnback


ModuleNotFoundError: No module named 'openai'

In [2]:

from collections import deque 
import osmnx as ox
import matplotlib.pyplot as plt
import numpy as np
import networkx as nx
import requests
import geopandas as gpd
import matplotlib.pyplot as plt
from IPython.display import JSON
import json
import re
import shutil
from shapely.geometry import Point, LineString
from shapely.ops import transform
from pyproj import Proj, Transformer
from math import atan2, degrees, radians, cos, sin
import matplotlib.colors as mcolors
import warnings
from geopy.distance import geodesic
import matplotlib.colors as mcolors
from loguru import logger
from datetime import datetime
import logging


In [ ]:
#This function is used to provide the main urban area Bbox of a city, with the shape set as a quadrilateral that encompasses the urban area
    
def define_city_bounds(city_name):
    # Use osmnx to download the road network data of the specified city
    city_graph = ox.graph_from_place(city_name, network_type='drive')
    
    # Use graph_to_gdfs to get the GeoDataFrame of nodes and edges
    gdf_nodes, gdf_edges = ox.graph_to_gdfs(city_graph)
    
    # Calculate the bounding box
    bounds = gdf_nodes.total_bounds  # Returns [minx, miny, maxx, maxy], i.e. [west, south, east, north]
    west, south, east, north = bounds
    
    # Define the coordinates of the four corners in the order of 1,2,3,4
    corners = [(west, north), (east, north), (east, south), (west, south)]
    
    # Plot the city road network and bounding box
    fig, ax = ox.plot_graph(city_graph, show=False, close=False)
    # Create a rectangle to represent the bounding box
    rectangle = plt.Rectangle((west, south), east - west, north - south, linewidth=1, edgecolor='r', facecolor='none')
    ax.add_patch(rectangle)

    # Plot for testing, comment out before actual run
    #plt.show()
    
    return corners



In [ ]:
# Initialize logger
# Generate random city routes
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

MAX_ATTEMPTS = 100  # Define the maximum number of attempts

def generate_city_routes(
    city_name: str,
    num_routes: int,
    distance_range: tuple,
):

    # Get city boundary
    logger.info(f"Getting boundary data for {city_name}...")
    gdf = ox.geocode_to_gdf(city_name)
    west, south, east, north = gdf.total_bounds

    # Build graph based on bounding box
    logger.info(f"Getting road network data for {city_name}...")
    graph = ox.graph_from_bbox(north, south, east, west, network_type="walk")
    logger.info("Road network data obtained successfully.")

    # Convert graph nodes to GeoDataFrame
    gdf_nodes = ox.graph_to_gdfs(graph, nodes=True, edges=False)
    rng = np.random.default_rng()
    routes = []
    start_nodes = set()  # Use set to improve lookup efficiency
    routes_lat_lon = []
    i = 1

    while i <= num_routes:
        sn = rng.choice(gdf_nodes.index)
        if sn in start_nodes:
            continue
        logger.info(f"Generating start-end pair {i}/{num_routes}, start node ID: {sn}")
        distance = distance_range[1] + 500  # Buffer distance

        # Extract subgraph centered at the start node from the main graph, node IDs remain the same
        subgraph = ox.truncate.truncate_graph_dist(
            graph, sn, max_dist=distance, weight='length'
        )
        sub_nodes = list(subgraph.nodes)
        valid_end_node = False
        attempts = 0

        while not valid_end_node and attempts < MAX_ATTEMPTS:
            if len(sub_nodes) > 1:
                en = rng.choice(sub_nodes)
                if en == sn:
                    attempts += 1
                    continue
                try:
                    length = nx.shortest_path_length(
                        subgraph,
                        source=sn,
                        target=en,
                        weight="length",
                    )
                    if distance_range[0] <= length <= distance_range[1]:
                        start_lat, start_lon = (
                            gdf_nodes.loc[sn]["y"],
                            gdf_nodes.loc[sn]["x"],
                        )
                        end_lat, end_lon = (
                            gdf_nodes.loc[en]["y"],
                            gdf_nodes.loc[en]["x"],
                        )
                        routes_lat_lon.append(
                            ((start_lat, start_lon), (end_lat, end_lon), length)
                        )
                        routes.append((sn, en, length))
                        start_nodes.add(sn)
                        logger.info(
                            f"Successfully generated route {i}/{num_routes}: start {sn}, end {en}, distance {length:.2f} meters"
                        )
                        valid_end_node = True
                        i += 1
                    else:
                        attempts += 1
                except (nx.NetworkXNoPath, nx.NodeNotFound):
                    attempts += 1
            else:
                logger.warning(f"Node {sn} is isolated, skipping.")
                break

        if attempts >= MAX_ATTEMPTS and not valid_end_node:
            logger.info(
                f"After {MAX_ATTEMPTS} attempts, no valid route could be found from node {sn}."
            )

    # Plot road network and routes
    fig, ax = ox.plot_graph(graph, show=False, close=False)
    for start_node, end_node, length in routes:
        # Get coordinates of start and end points
        start_point = gdf_nodes.loc[start_node]
        end_point = gdf_nodes.loc[end_node]
        # Plot start and end points
        ax.scatter(start_point['x'], start_point['y'], c='red', s=50, zorder=5)
        ax.scatter(end_point['x'], end_point['y'], c='green', s=50, zorder=5)
        # Plot route
        try:
            route = nx.shortest_path(graph, source=start_node, target=end_node, weight='length')
            route_nodes = gdf_nodes.loc[route]
            ax.plot(route_nodes['x'], route_nodes['y'], c='blue')
        except nx.NetworkXNoPath:
            logger.warning(f"No path between node {start_node} and {end_node}, skipping.")
            continue

    plt.show()

    return routes, routes_lat_lon

# Test function
#city_name = "Toronto, Canada"
city_name = 'Paris, France'
distance_range = (500, 2000)
routes, routes_lat_lon = generate_city_routes(city_name, 1100, distance_range)






![Previous cell results showed as below](output.png)

In [ ]:
def call_directions_api(routes):
    api_key = ""  # Please replace with your actual API key
    headers = {
        "Content-Type": "application/json; charset=utf-8",
        "Accept": "application/json, application/geo+json, application/gpx+xml, img/png; charset=utf-8",
        "Authorization": api_key,
    }
    results = []

    # Use a queue to record the timestamp of each request
    request_times = deque()
    max_requests = 40  # Maximum number of requests per 60 seconds
    time_window = 60  # Time window (seconds)

    for index, (start, end, _) in enumerate(routes):
        current_time = time.time()

        # Remove request timestamps outside the time window
        while request_times and current_time - request_times[0] > time_window:
            request_times.popleft()

        # If the number of requests reaches the limit, wait until the next request can be sent
        if len(request_times) >= max_requests:
            wait_time = time_window - (current_time - request_times[0])
            print(f"Reached the limit of {max_requests} requests per minute, waiting {wait_time:.2f} seconds...")
            time.sleep(wait_time)
            continue  # Continue the loop and recheck the request count

        body = {
            "coordinates": [
                [start[1], start[0]],  # Longitude first, latitude second
                [end[1], end[0]],
            ]
        }

        # Send API request
        response = requests.post(
            "https://api.openrouteservice.org/v2/directions/foot-walking/geojson",
            json=body,
            headers=headers,
        )

        # Record request time
        request_times.append(current_time)

        # Parse and store the result
        if response.status_code == 200:
            geojson = response.json()  # Parse the response as JSON
            results.append(geojson)  # Add to the result list
        else:
            results.append({"error": response.text})  # Store error information

        time.sleep(0.1)  # Optional: add a short delay to avoid sending requests too frequently

    return results


# Call the function
api_results = call_directions_api(routes_lat_lon)

# Print the returned geojson results
for index, result in enumerate(api_results):
    if 'error' not in result:
        print(f"Result {index + 1}: Route GeoJSON")
        # Use IPython.display.JSON to display JSON data
        display(JSON(result))
    else:
        print(f"Result {index + 1}: Error - {result['error']}")


In [ ]:
# New API call function

def call_directions_api(routes):

    api_key = "5b3ce3597851110001cf62485fc5eb75a4e34c5285ae485ab9d97bcf"  # Please replace with your actual API key

    headers = {
        "Content-Type": "application/json; charset=utf-8",
        "Accept": "application/json, application/geo+json, application/gpx+xml, img/png; charset=utf-8",
        "Authorization": api_key,
    }
    results = []
    success_count = 0  # Record the number of successful results

    # Use a queue to record the timestamp of each request
    request_times = deque()
    max_requests = 40  # Maximum number of requests per 60 seconds
    time_window = 60  # Time window (seconds)
    min_interval = time_window / max_requests  # Minimum interval between requests

    index = 0  # Initialize index
    retries = {}  # Record the number of retries for each request
    max_retries = 3  # Maximum number of retries per request

    while index < len(routes):
        start, end, _ = routes[index]
        current_time = time.time()

        # Remove request timestamps outside the time window
        while request_times and current_time - request_times[0] >= time_window:
            request_times.popleft()

        # If the number of requests reaches the limit, wait until the next request can be sent
        if len(request_times) >= max_requests:
            wait_time = time_window - (current_time - request_times[0])
            print(f"Reached the limit of {max_requests} requests per minute, waiting {wait_time:.2f} seconds...")
            time.sleep(wait_time)
            # Update current time and recalculate request timestamps
            current_time = time.time()
            while request_times and current_time - request_times[0] >= time_window:
                request_times.popleft()
            continue  # Continue loop

        # Check if waiting is needed to meet the minimum request interval
        if request_times:
            elapsed_since_last_request = current_time - request_times[-1]
            if elapsed_since_last_request < min_interval:
                time_to_wait = min_interval - elapsed_since_last_request
                time.sleep(time_to_wait)
                current_time = time.time()

        # Record request time before sending the request
        request_times.append(current_time)

        body = {
            "coordinates": [
                [start[1], start[0]],  # Longitude first, latitude second
                [end[1], end[0]],
            ]
        }

        # Send API request
        response = requests.post(
            "https://api.openrouteservice.org/v2/directions/foot-walking/geojson",
            json=body,
            headers=headers,
        )

        # Parse and store the result
        if response.status_code == 200:
            geojson = response.json()  # Parse the response as JSON
            results.append(geojson)  # Add to the result list
            success_count += 1  # Increase success count by 1
            print(f"Successfully obtained result {index + 1}, total successful: {success_count}.")
            index += 1  # Process the next request
        elif response.status_code == 429:
            # Handle rate limit error, wait and retry
            retry_after = int(response.headers.get('Retry-After', 60))
            print(f"Received 429 error, waiting {retry_after} seconds before retrying request {index + 1}...")
            time.sleep(retry_after)
            # Remove the previously recorded request timestamp
            request_times.pop()
            # Do not increase the index, retry the current request
            continue
        else:
            # Check if already retried
            retries.setdefault(index, 0)
            if retries[index] < max_retries:
                retries[index] += 1
                print(f"Error occurred when requesting result {index + 1}, status code {response.status_code}, retry count {retries[index]}...")
                # Remove the previously recorded request timestamp
                request_times.pop()
                time.sleep(2)  # Wait 2 seconds before retrying
                continue
            else:
                # Maximum retries reached, record error information
                error_info = {
                    "error": response.text,
                    "status_code": response.status_code
                }
                results.append(error_info)
                print(f"Request {index + 1} failed, error information recorded.")
                index += 1  # Process the next request

    print(f"All requests processed, total successful: {success_count}.")
    return results


api_results = call_directions_api(routes_lat_lon)

for index, result in enumerate(api_results):
    if 'error' not in result:
        print(f"Result {index + 1}: Route GeoJSON")
        display(JSON(result))
    else:
        print(f"Result {index + 1}: Error - {result['error']}")

In [13]:
def save_geojsons_and_extract_instructions(api_results):
    data_set_dir = 'data_set'

    # Ensure the data_set directory exists
    if not os.path.exists(data_set_dir):
        os.makedirs(data_set_dir)

    for index, geojson_data in enumerate(api_results):
        # Create a directory for each geojson
        geojson_dir = os.path.join(data_set_dir, str(index))
        if not os.path.exists(geojson_dir):
            os.makedirs(geojson_dir)

        # Save geojson data
        geojson_path = os.path.join(geojson_dir, 'route.geojson')
        with open(geojson_path, 'w') as file:
            json.dump(geojson_data, file, indent=4)

        # Read the just saved geojson file and extract instructions
        instructions = []
        if 'features' in geojson_data:
            for feature in geojson_data['features']:
                if 'properties' in feature and 'segments' in feature['properties']:
                    segments = feature['properties']['segments']
                    for segment in segments:
                        for step in segment['steps']:
                            name = step.get('name', 'N/A')
                            instruction = step.get('instruction', 'No instruction provided')
                            distance = step.get('distance', 'Unknown distance')
                            time = step.get('duration', 'Unknown time')

                            # Format instruction information
                            step_info = f"Name: {name}, Instruction: {instruction}, Distance: {distance} meters, Time: {time} seconds"
                            instructions.append(step_info)

        # Save all instructions to a txt file
        instruction_file_path = os.path.join(geojson_dir, 'instructions.txt')
        with open(instruction_file_path, 'w') as file:
            for instruction in instructions:
                file.write(instruction + "\n")


save_geojsons_and_extract_instructions(api_results)


In [ ]:
import os

def format_instructions_to_paragraph(file_path):
    """Read instructions from file and format each instruction as a single line."""
    instructions = []
    try:
        with open(file_path, 'r', encoding='utf-8') as file:
            lines = file.readlines()
    except FileNotFoundError:
        print(f"File not found: {file_path}")
        return []

    for line in lines:
        # Use regular expressions to precisely match and extract instruction data
        match = re.match(r"Name: (.*?), Instruction: (.*?), Distance: (.*? meters), Time: (.*? seconds)", line.strip())
        if not match:
            continue

        name, instruction, distance, time = match.groups()

        # Format output string based on whether the name is "-"
        if name.strip() == "-":
            formatted_instruction = f"{instruction}, continue for {distance} and taking about {time}."
        else:
            formatted_instruction = f"{instruction} on {name}, continue for {distance} and taking about {time}."

        instructions.append(formatted_instruction)

    return instructions




def extract_and_format_instructions():
    data_set_dir = "data_set"
    natural_instructions = []

    if not os.path.exists(data_set_dir):
        print("Dataset directory does not exist.")
        return natural_instructions

    for folder in os.listdir(data_set_dir):
        folder_path = os.path.join(data_set_dir, folder)
        instructions_file_path = os.path.join(folder_path, "instructions.txt")
        output_file_path = os.path.join(folder_path, "natural_instructions.txt")

        # Process instructions file and save the formatted lines
        formatted_instructions = format_instructions_to_paragraph(instructions_file_path)
        if formatted_instructions:
            with open(output_file_path, 'w', encoding='utf-8') as output_file:
                for instruction in formatted_instructions:
                    output_file.write(instruction + "\n")

            # Add to the list of all formatted instructions
            natural_instructions.append("\n".join(formatted_instructions))

    return natural_instructions

# Call the function and print the results
natural_instructions_list = extract_and_format_instructions()
for instruction in natural_instructions_list:
    print(instruction)
    print("------next instruction------")


Head south, continue for 304.5 meters and taking about 219.3 seconds.
Turn slight left, continue for 10.5 meters and taking about 7.6 seconds.
Turn slight right, continue for 407.0 meters and taking about 293.0 seconds.
Keep right, continue for 94.8 meters and taking about 68.2 seconds.
Turn left, continue for 15.0 meters and taking about 10.8 seconds.
Keep right, continue for 55.3 meters and taking about 39.8 seconds.
Keep right, continue for 31.2 meters and taking about 22.5 seconds.
Turn right, continue for 4.1 meters and taking about 3.0 seconds.
Turn left, continue for 4.3 meters and taking about 3.1 seconds.
Turn left, continue for 3.7 meters and taking about 2.7 seconds.
Turn right, continue for 28.4 meters and taking about 20.4 seconds.
Turn left, continue for 7.7 meters and taking about 5.5 seconds.
Turn right, continue for 25.4 meters and taking about 18.3 seconds.
Turn left, continue for 32.9 meters and taking about 23.7 seconds.
Turn right, continue for 16.4 meters and taki

In [15]:
def parse_instruction(instruction):
    """Parse a single navigation instruction extracting action type, direction, street name (if any), distance, and duration."""
    results = {
        'actions': re.findall(r"\b(turn|continue|walk|head|arrive)\b", instruction, re.IGNORECASE),
        'directions': re.findall(r"\b(north|south|east|west|left|right|sharp left|sharp right|northeast|northwest|southeast|southwest)\b", instruction, re.IGNORECASE),
        'start_streets': [],
        'end_streets': [],
        'distances': [float(num) for num in re.findall(r"(\d+\.\d+|\d+) meters", instruction)],
        'durations': [float(num) for num in re.findall(r"(\d+\.\d+|\d+) seconds", instruction)]
    }

    # Extract street names based on prepositions
    street_matches = re.finditer(r"\b(to|onto|on|at) ([A-Z][\w-]+)\b", instruction)
    for match in street_matches:
        preposition = match.group(1)
        street_name = match.group(2)
        if preposition == 'on':
            results['start_streets'].append(street_name)
        else:
            results['end_streets'].append(street_name)

    return results

def process_instructions(instructions):
    """ Process a series of navigation instructions """
    results = []
    for instruction in instructions:
        parsed_data = parse_instruction(instruction)
        results.append(parsed_data)
    return results

def process_dataset():
    data_set_dir = "data_set"
    all_results = []

    for folder in os.listdir(data_set_dir):
        folder_path = os.path.join(data_set_dir, folder)
        input_file_path = os.path.join(folder_path, "natural_instructions.txt")
        output_file_path = os.path.join(folder_path, "instructions_parse.txt")

        if os.path.isfile(input_file_path):
            with open(input_file_path, 'r', encoding='utf-8') as file:
                instructions = [line.strip() for line in file if line.strip()]

            parsed_instructions = process_instructions(instructions)

            with open(output_file_path, 'w', encoding='utf-8') as file:
                # Join the parsed instructions into a single string with a comma after each, except the last
                for i, instruction in enumerate(parsed_instructions):
                    if i < len(parsed_instructions) - 1:
                        file.write(json.dumps(instruction, ensure_ascii=False) + ",\n")
                    else:
                        file.write(json.dumps(instruction, ensure_ascii=False) + "\n")

            all_results.extend(parsed_instructions)

    return all_results


results = process_dataset()
for result in results:
    print(json.dumps(result, indent=4))







{
    "actions": [
        "Head",
        "continue"
    ],
    "directions": [
        "south"
    ],
    "start_streets": [],
    "end_streets": [],
    "distances": [
        304.5
    ],
    "durations": [
        219.3
    ]
}
{
    "actions": [
        "Turn",
        "continue"
    ],
    "directions": [
        "left"
    ],
    "start_streets": [],
    "end_streets": [],
    "distances": [
        10.5
    ],
    "durations": [
        7.6
    ]
}
{
    "actions": [
        "Turn",
        "continue"
    ],
    "directions": [
        "right"
    ],
    "start_streets": [],
    "end_streets": [],
    "distances": [
        407.0
    ],
    "durations": [
        293.0
    ]
}
{
    "actions": [
        "continue"
    ],
    "directions": [
        "right"
    ],
    "start_streets": [],
    "end_streets": [],
    "distances": [
        94.8
    ],
    "durations": [
        68.2
    ]
}
{
    "actions": [
        "Turn",
        "continue"
    ],
    "directions": [
        "

In [ ]:
# Turning functionality module

# Input a bunch of edges and a target direction, return the edge closest to the target direction
    
def calculate_bearing(lat1, lon1, lat2, lon2):
    """Calculate the bearing between two geographical points."""
    lat1, lon1, lat2, lon2 = map(radians, [lat1, lon1, lat2, lon2])
    delta_lon = lon2 - lon1
    x = cos(lat2) * sin(delta_lon)
    y = cos(lat1) * sin(lat2) - sin(lat1) * cos(lat2) * cos(delta_lon)
    initial_bearing = atan2(x, y)
    bearing = (degrees(initial_bearing) + 360) % 360
    return bearing

def get_first_points(G, node_id):
    """Retrieve and calculate bearings from the first points of all linestrings connected to the specified node."""
    bearings = {}
    for neighbor in G.neighbors(node_id):
        edge_data = G.get_edge_data(node_id, neighbor, 0)
        if 'geometry' in edge_data:
            line = edge_data['geometry']
        else:
            # Construct a LineString from node coordinates when geometry is not available
            point_u = (G.nodes[node_id]['x'], G.nodes[node_id]['y'])
            point_v = (G.nodes[neighbor]['x'], G.nodes[neighbor]['y'])
            line = LineString([point_u, point_v])
            #print("This line without geometry is", line)
        if isinstance(line, LineString) and len(line.coords) > 1:
            point1 = (G.nodes[node_id]['y'], G.nodes[node_id]['x'])
            
            first_point = line.coords[1] # Here, use the first point of the new street instead of the current origin as the start of the new street walk
                                         # Try using the origin as the new direction point here?
            
            bearing = calculate_bearing(point1[0], point1[1], first_point[1], first_point[0])
            bearings[neighbor] = (bearing, first_point)
        else:
            print(f"LineString between {node_id} and {neighbor} is not valid.")
    
    print(bearings)
    return bearings   # Here, return the angle with the first point and the coordinates of the first point


def update_heading(current_heading, change_direction):
    """Update the heading based on the specified direction change, including slight and sharp turns."""
    direction_to_degrees = {
        'north': 0, 'northeast': 45, 'east': 90, 'southeast': 135,
        'south': 180, 'southwest': 225, 'west': 270, 'northwest': 315,
        'left': (current_heading - 75) % 360,  # 60 degrees left turn
        'right': (current_heading + 75) % 360,  # 60 degrees right turn
        'slight left': (current_heading - 30) % 360,  # 30 degrees slight left turn
        'slight right': (current_heading + 30) % 360,  # 30 degrees slight right turn
        'sharp left': (current_heading - 100) % 360,  # 100 degrees sharp left turn
        'sharp right': (current_heading + 100) % 360  # 100 degrees sharp right turn
    }
    return direction_to_degrees.get(change_direction, current_heading)




In [ ]:

print(calculate_bearing(49.404323,8.623914,49.40432299999999, 8.623914))


In [ ]:
# Module for walking along the street
warnings.filterwarnings("ignore", category=FutureWarning, module="osmnx")
def walk_along_street(coordinates, direction, move_distance = 0):

    # Unpack latitude and longitude
    start_lat, start_lon = coordinates
    
    # Define transformers for coordinate conversion
    # transformer_to_utm = Transformer.from_proj(Proj(proj='latlong', datum='WGS84'), Proj(proj='utm', zone=32, ellps='WGS84', preserve_units=False))
    # transformer_to_latlong = Transformer.from_proj(Proj(proj='utm', zone=32, ellps='WGS84', preserve_units=False), Proj(proj='latlong', datum='WGS84'))

    # Transformer from WGS84 latitude/longitude (EPSG:4326) to UTM zone 12N (EPSG:32612)
    transformer_to_utm = Transformer.from_crs("EPSG:4326", "EPSG:32189", always_xy=True)

    # Transformer from UTM zone 12N (EPSG:32612) back to WGS84 latitude/longitude (EPSG:4326)
    transformer_to_latlong = Transformer.from_crs("EPSG:32189", "EPSG:4326", always_xy=True)
    
    # Load the street network
    G = ox.graph_from_point((start_lat, start_lon), dist=500, network_type='walk', simplify=True)

    # Use nearest_node to find the nearest node
    nearest_node = ox.distance.nearest_nodes(G, start_lon, start_lat)

    # Get all edges starting from this node, ensuring u node ID matches nearest_node
    edges = [(u, v, key, data) for u, v, key, data in G.edges(nearest_node, data=True, keys=True) if u == nearest_node]

    edges_with_bearing = []
    for u, v, key, data in edges:
        # Get the latitude and longitude information of the nodes from the graph
        u_lat, u_lon = G.nodes[u]['y'], G.nodes[u]['x']
        v_lat, v_lon = G.nodes[v]['y'], G.nodes[v]['x']

        # Calculate bearing
        bearing = calculate_bearing(u_lat, u_lon, v_lat, v_lon)

        # Add bearing to edge information
        edges_with_bearing.append((u, v, key, data, bearing))

    #print(edges_with_bearing)

    # Find the edge with the closest bearing to the target direction
    nearest_edge = None
    min_angle_difference = float('inf')
    for u, v, key, data, bearing in edges_with_bearing:
        angle_difference = min(abs(bearing - direction), 360 - abs(bearing - direction))
        if angle_difference < min_angle_difference:
            min_angle_difference = angle_difference
            nearest_edge = (u, v, key, data, bearing)
    
    #print(nearest_edge)    
    # Unpack the edge data
    u, v, key, edge_data, edge_bearing = nearest_edge
    

    geometry = (
        edge_data["geometry"]
        if "geometry" in edge_data
        else LineString(
            [[G.nodes[u]["x"], G.nodes[u]["y"]], [G.nodes[v]["x"], G.nodes[v]["y"]]],
        )
    )
    #print('current edge direction:',nearest_edge)
    
    edge_bearing = calculate_bearing(G.nodes[u]['y'], G.nodes[u]['x'], G.nodes[v]['y'], G.nodes[v]['x'])
    angle_difference = abs(direction - edge_bearing)
    if angle_difference < 90:
        forward = True
    else:
        forward = False
    #print("Currently processing geometry while walking",geometry)
    # Calculate and mark the point
    if geometry:
        # Convert the geometry to UTM
        geometry_utm = transform(lambda x, y: transformer_to_utm.transform(x, y), geometry)
        total_length = geometry_utm.length
        #print(f"Total street length: {total_length} meters")
        
        start_point = Point(start_lon, start_lat)
        start_point_utm = transform(lambda x, y: transformer_to_utm.transform(x, y), start_point)
        #print("Input start point",start_point,"Input start point utm",start_point_utm)
        nearest_point_on_line = geometry_utm.interpolate(geometry_utm.project(start_point_utm))
        
        move_fraction = move_distance / total_length
        #print(f"Move distance fraction: {move_fraction} (fraction of total length)")
        
        # Adjust the move distance based on direction
        direction_multiplier = 1 if forward else -1
        mark_point = geometry_utm.interpolate(geometry_utm.project(nearest_point_on_line) + total_length * move_fraction * direction_multiplier)
        #print("Mark point before coordinate transformation",mark_point)
        mark_point_geo = transform(lambda x, y: transformer_to_latlong.transform(x, y), mark_point)
        #print("Mark point after coordinate transformation",mark_point_geo)
        end_point = (mark_point_geo.y, mark_point_geo.x) #Can these people please unify the order of latitude and longitude, it's so annoying
        #print("Direction before angle calculation",direction)
        #print("Start point before angle calculation:",start_point, "Mark point before angle calculation:",mark_point_geo)
        new_direction = calculate_bearing(start_lat, start_lon, mark_point_geo.y, mark_point_geo.x)
        #print("Direction after angle calculation",new_direction)
        #print("Current location:", endpoint)
        #print(new_direction)
        
        # # Plot the map and marked point
  
        # fig, ax = ox.plot_graph(G, show=False, close=False)
        # ax.scatter([start_lon], [start_lat], c='yellow', s=20, zorder=3)  # Yellow indicates the starting point
        # ax.scatter([nearest_point_on_line.x], [nearest_point_on_line.y], c='blue', s=20, zorder=3)  # Blue indicates the nearest point on the street
        # ax.scatter([mark_point_geo.x], [mark_point_geo.y], c='red', s=20, zorder=3)  # Red indicates the marked point
        
        # # Draw a line with an arrow from the start point to the marked point
        # ax.annotate('', xy=(mark_point_geo.x, mark_point_geo.y), xytext=(start_lon, start_lat),
        #             arrowprops=dict(facecolor='green', edgecolor='green', arrowstyle='->', lw=2))

        # plt.show()

        if(move_distance > total_length):
            actual_moved_distance = total_length
        else:
            actual_moved_distance = move_distance

        if(new_direction == 0):
            print("There was a problem with this walk")
        
        

        #print("Output direction",new_direction)
        #print("Actual moved distance",actual_moved_distance)

        return end_point, new_direction, actual_moved_distance
        #return end_point
    else:
        print("No detailed geometry data available.")


#new_status = walk_along_street((49.4203935, 8.6886011), forward=False, move_distance = 40)
#new_status
#endpoint, new_direction = walk_along_street((49.40379, 8.623154), forward=True, move_distance = 20)
#endpoint, new_direction = walk_along_street((49.4461847, 8.6736525), forward=False, move_distance = 15.4)


#endpoint, new_direction = walk_along_street((49.403853, 8.623224), forward=True, move_distance = 20)
endpoint, new_direction, actual_moved_distance = walk_along_street(
    (43.750781, -79.281252), 270, move_distance=97
)


In [ ]:
import osmnx as ox
from shapely.geometry import Point
import matplotlib.pyplot as plt

def visualize_nearest_edge(lat, lon):
    ox.config(use_cache=True, log_console=True)
    point = (lat, lon)
    G = ox.graph_from_point(point, dist=200, network_type='walk', simplify=False)
    u, v, key = ox.distance.nearest_edges(G, X=lon, Y=lat)
    edge_data = G.get_edge_data(u, v, key)

    print("Edge Data:", edge_data)

    # Ensure the color logic is correct
    ec = ['r' if (u2, v2, k2) == (u, v, key) else '#999999' for u2, v2, k2 in G.edges(keys=True)]
    print("Color list:", ec)  # Debug color list

    fig, ax = ox.plot_graph(G, edge_color=ec, edge_linewidth=3, node_size=0, show=False, close=False)
    plt.show()

# Example call
lat, lon = 49.404251, 8.623892  # Example coordinates
visualize_nearest_edge(lat, lon)

# Utility function: read instructions_parse.txt from the specified folder and return the parsed instruction data
def read_instructions(folder_path):
    file_path = os.path.join(folder_path, 'instructions_parse.txt')
    try:
        with open(file_path, 'r') as file:
            # Read the entire file content
            data = file.read()
            # Manually convert the content to valid JSON
            data = "[" + data.replace("}\n{", "},\n{") + "]"
            # Parse the JSON data
            instructions = json.loads(data)
            return instructions
    except FileNotFoundError:
        print("File not found:", file_path)
        return None
    except json.JSONDecodeError:
        print("File content format error")
        return None
    except Exception as e:
        print("Error occurred while reading the file:", str(e))
        return None



#results = read_instructions('data_set/0')
#print(results)


In [ ]:
# Utility function: For a node connected to multiple streets, return all connected streets and their bearings.
def get_connected_streets_from_coords(coords, network_type='walk'):
    lat, lon = coords
    G = ox.graph_from_point((lat, lon), dist=200, network_type=network_type)
    node_id = ox.nearest_nodes(G, lon, lat)
    connected_streets = []

    color_cycle = plt.get_cmap('tab10')  # Use Matplotlib's color cycle to ensure color contrast
    color_index = 0

    # Check all edges from and to the node
    for u, v, key, edge_data in G.edges(nbunch=[node_id], keys=True, data=True):
        if 'geometry' in edge_data:
            line = edge_data['geometry']
        else:
            point_u = (G.nodes[u]['y'], G.nodes[u]['x'])
            point_v = (G.nodes[v]['y'], G.nodes[v]['x'])
            line = LineString([point_u, point_v])

        if u == node_id:  # The start point is node_id
            start_point = line.coords[0]
            end_point = line.coords[-1]
        else:  # The end point is node_id, calculate in reverse
            start_point = line.coords[-1]
            end_point = line.coords[0]

        bearing = calculate_bearing(start_point[0], start_point[1], end_point[0], end_point[1])
        street_name = edge_data.get('name', 'Unnamed Street')
        color = color_cycle(color_index % 10)
        connected_streets.append((street_name, bearing, line, color))
        color_index += 1

    return connected_streets

coords = (49.40429079999999, 8.6238435)  # Example coordinates
streets = get_connected_streets_from_coords(coords)
for street in streets:
    print(f"Street: {street[0]}, Bearing: {street[1]}°")

In [ ]:
# New turning logic

def turn_on_direction(current_location, current_direction, new_direction):

    # Get the edges connected to the current point
    G = ox.graph_from_point(current_location, dist=500, network_type='walk')
    nearest_node = ox.distance.nearest_nodes(G, current_location[1], current_location[0])

    # Get all edges starting from this node, ensuring u node ID matches nearest_node
    edges = [(u, v, key, data) for u, v, key, data in G.edges(nearest_node, data=True, keys=True) if u == nearest_node]

    # Convert the direction of new_direction to a number, and calculate the new direction to use
    new_direction = update_heading(current_direction, new_direction)


    # Calculate the bearing of each edge
    edges_with_bearing = []
    for u, v, key, data in edges:
        # Get the latitude and longitude information of the nodes from the graph
        u_lat, u_lon = G.nodes[u]['y'], G.nodes[u]['x']
        v_lat, v_lon = G.nodes[v]['y'], G.nodes[v]['x']

        # Calculate the bearing
        bearing = calculate_bearing(u_lat, u_lon, v_lat, v_lon)

        # Add the bearing to the edge information
        edges_with_bearing.append((u, v, key, data, bearing))
    
    # Find the edge closest to the target direction
    nearest_edge = None
    min_angle_difference = float('inf')
    for u, v, key, data, bearing in edges_with_bearing:
        angle_difference = min(abs(bearing - new_direction), 360 - abs(bearing - new_direction))
        if angle_difference < min_angle_difference:
            min_angle_difference = angle_difference
            nearest_edge = (u, v, key, data, bearing)
    
    # Unpack edge data
    u, v, key, edge_data, edge_bearing = nearest_edge
    geometry = (
        edge_data["geometry"]
        if "geometry" in edge_data
        else LineString(
            [[G.nodes[u]["x"], G.nodes[u]["y"]], [G.nodes[v]["x"], G.nodes[v]["y"]]],
        )
    )

    # Convert the coordinates of point u to a Point object
    u_point = Point(G.nodes[u]['y'], G.nodes[u]['x'])
    final_new_point = (u_point.x, u_point.y)
    final_new_direction = edge_bearing


    return final_new_direction, final_new_point





In [ ]:
# Module for executing instructions
def execute_commands(commands, current_state, current_folder_path):
    # Initialize current position and direction
    current_position = current_state['current_coordinates']  # Current coordinates (latitude and longitude)
    current_direction = current_state['current_direction']  # Current heading/direction
    current_street = current_state['current_street']  # Current street name, might be empty
    # Here, a pre-test module should be added to prevent the starting point from being set at an intersection. The first instruction can be pre-read to determine the street and heading at the starting point.

    for command in commands:
        # Check for start streets
        # if command['start_streets']:
        #     for street in command['start_streets']:
        #         locate_start_street(street)  # Locate the start street
        
        # # Check for end streets
        # if command['end_streets']:
        #     for street in command['end_streets']:
        #         locate_end_street(street)  # Locate the end street
        
        # Check for actions and execute corresponding functions
        for action in command['actions']:
            if action == 'Arrive':
                full_route = generate_answer(route, current_folder_path)
                print("Arrived at the destination!")
                
                return full_route

            if action in ['Turn','Head'] and command['directions']:
                direction = command['directions'][0]  # Get the first direction element
                print("Currently executing command", action, "direction:", direction)
                #print("Current direction and position", current_direction, current_position)
                
                # newpoint = process_direction_change(current_position, current_direction, direction)  # Update direction function
                # current_direction = newpoint[0]
                # current_position = newpoint[1]
                # first_point = newpoint[2]

                new_turn_on_direction, new_turn_on_start_point = turn_on_direction(current_position, current_direction, direction)
                #print("Direction and position after turning", new_turn_on_direction, new_turn_on_start_point)

                current_direction = new_turn_on_direction
                current_posisiton = new_turn_on_start_point

                route.append(current_position) # The function still stays at the original point, but the record function takes the next point
                #print(current_position, current_direction, first_point)
            
            if action == 'continue' and command['distances']:

                distance = command['distances'][0]  # Get the distance
                print("Currently executing command", action, "distance:", distance)
                #print(command['directions'][0])
                if command['directions']:
                    direction = update_heading(current_direction, command['directions'][0])
                else:
                    direction = current_direction
                #print("Current direction after first walk", direction)
                
                if distance > 0:  # Here, 1 is used to tolerate some small errors, may need to be changed
                    #new_direction, current_position, new_direction_first_point = process_direction_change(current_position, current_direction, current_direction)
                    new_turn_on_direction_in_walking, new_turn_on_start_point_in_walking = turn_on_direction(current_position, current_direction, current_direction)
                    endpoint, new_direction, actual_moved_distance = walk_along_street(new_turn_on_start_point_in_walking, new_turn_on_direction_in_walking, distance)  # Function to walk along the street
                    #print("Distance walked this time", actual_moved_distance)
                    current_position = endpoint
                    current_direction = new_direction
                    route.append(current_position)
                    distance = distance - actual_moved_distance
                    #print("Remaining distance after this walk", distance)
                    while distance > 1:
                        #new_direction, current_position, new_direction_first_point = process_direction_change(current_position, current_direction, current_direction)
                        new_direction, new_current_position = turn_on_direction(current_position, current_direction, current_direction)
                        new_turn_on_direction_in_walking, new_turn_on_start_point_in_walking = turn_on_direction(new_current_position, new_direction, new_direction)
                        endpoint, new_direction, move_distance = walk_along_street(current_position, new_direction, distance)  # Function to walk along the street
                        #print("Latest heading after each walk", new_direction)
                        current_position = endpoint
                        current_direction = new_direction
                        route.append(current_position)
                        distance = distance - move_distance




# The following is the automated testing code, which is different from local testing. Automated testing code is used to report accuracy, etc.
initial_state = {
    'current_coordinates': (0, 0),
    'current_direction': 0,  # Assuming starting from true north
    'current_street': None  # Initially, there might not be any street information
}

dataset_folder = 'data_set'

# Comment out when not in use
target_folder = '7'

for folder_name in sorted(os.listdir(dataset_folder), key=lambda x: int(x)):

    # if folder_name == '5':
    #     print("Already processed folders before", folder_name)
    #     break

    # if folder_name != target_folder:  # Only process the specified folder
    #     continue

    # The above two parts are for targeted debugging

    folder_path = os.path.join(dataset_folder, folder_name)
    route = []

    print("Currently processing folder", folder_path)
    
    # Make sure it is a folder
    if os.path.isdir(folder_path):
        # Call get_start_end_points function
        start_end_point = get_start_end_points(folder_name)
        parse_instructions = read_instructions(folder_path)

        initial_state['current_coordinates'] = start_end_point['start']
        initial_state['current_coordinates'] = (initial_state['current_coordinates'][1], initial_state['current_coordinates'][0])
        route.append(initial_state['current_coordinates'])
        #print(parse_instructions)

        current_full_route = execute_commands(parse_instructions, initial_state, folder_path)

        # Specify the input and output file paths
        input_file_path = os.path.join(folder_path, 'answer_newway.geojson')  # Replace with your input file path
        output_file_path = os.path.join(folder_path, 'answer_combin.geojson')  # Replace with your output file path
        print("Current input and output file paths", input_file_path, output_file_path)
        # Read GeoJSON data
        geojson_data = read_geojson(input_file_path)

        # Process and merge GeoJSON features
        merged_geojson = merge_line_features(geojson_data)

        # Save the new GeoJSON data to file
        save_geojson(merged_geojson, output_file_path)

        print("GeoJSON data has been processed and saved to:", output_file_path)
            












# ]






In [ ]:
# Utility function: check if the number of In_edges and Out_edges at a point are equal; return True if so, otherwise return False

def check_edges_balance(lat, lon):

    ox.config(use_cache=True, log_console=True)
    G = ox.graph_from_point((lat, lon), dist=500, network_type='walk', simplify=True)
    nearest_node = ox.distance.nearest_nodes(G, lon, lat)
    in_edges = G.in_edges(nearest_node, keys=True)
    out_edges = G.out_edges(nearest_node, keys=True)
    total_edges = G.edges(nearest_node, keys=True)
    print(in_edges, out_edges, total_edges)
    if len(in_edges) == len(out_edges) == len(total_edges):
        return True
    else:
        return False

def visualize_connected_edges(lat, lon):
    # Configure OSMnx
    ox.config(use_cache=True, log_console=True)

    # Get the walking network centered at the given point
    G = ox.graph_from_point((lat, lon), dist=100, network_type='walk', simplify=False)

    # Find the nearest node
    nearest_node = ox.distance.nearest_nodes(G, lon, lat)

    # Get all edges connected to the node (including in-edges and out-edges)
    edges_in = list(G.in_edges(nearest_node, data=True, keys=True))
    edges_out = list(G.out_edges(nearest_node, data=True, keys=True))

    # Combine the two edge lists
    edges = edges_in + edges_out

    # Create a color map
    color_map = plt.cm.get_cmap('hsv', len(edges) + 1)  # HSV color map, +1 to ensure no color repetition

    # Plot the graph
    fig, ax = ox.plot_graph(G, show=False, close=False, edge_color='#888888', node_size=0)

    # Assign a different color to each connected edge and plot
    for i, (u, v, key, data) in enumerate(edges):
        color = mcolors.to_hex(color_map(i))
        # Extract the geometry of the edge
        if 'geometry' in data:
            xs, ys = data['geometry'].xy
        else:
            # If no geometry info, draw a line using node coordinates
            xs = [G.nodes[u]['x'], G.nodes[v]['x']]
            ys = [G.nodes[u]['y'], G.nodes[v]['y']]
        ax.plot(xs, ys, color=color, linewidth=3, alpha=0.7)
    print(edges)
    plt.show()


visualize_connected_edges(49.404219, 8.623688)


In [ ]:
import osmnx as ox
import numpy as np
from shapely.geometry import Point
from math import radians, cos, sin, atan2, degrees

def adjust_direction(direction):
    dir_mapping = {'north': 0, 'northeast': 45, 'east': 90, 'southeast': 135, 'south': 180, 'southwest': 225, 'west': 270, 'northwest': 315}
    return dir_mapping.get(direction.lower(), None)

def correct_position(initial_state, command, G):
    # Step 1: Extract the first element of command
    first_step = command[0]
    street_name = first_step['start_streets'][0]

    # Step 2: Fuzzy matching for street
    target_street = None
    for edge in G.edges(data=True):
        if edge[2]['name'][:3] == street_name[:3]:
            target_street = edge
            break
    
    if not target_street:
        print("No street found matching the criteria.")
        return initial_state

    # Step 3: Find the nearest point on the street
    point = Point(initial_state['current_coordinates'][1], initial_state['current_coordinates'][0])  # (lon, lat) for Point
    street_geom = target_street[2]['geometry']
    nearest_point = street_geom.interpolate(street_geom.project(point))
    new_coords = (nearest_point.y, nearest_point.x)

    # Step 4: Determine the direction and adjust forward variable
    new_direction = adjust_direction(first_step['directions'][0])
    street_direction = calculate_bearing(*street_geom.coords[0], *street_geom.coords[-1])
    forward = True if abs(new_direction - street_direction) < 180 else False

    # Step 5: Determine the next point based on forward value
    if forward:
        next_point = (street_geom.coords[0][1], street_geom.coords[0][0])  # First point in direction of street
    else:
        next_point = (street_geom.coords[-1][1], street_geom.coords[-1][0])  # Last point, i.e., first point in opposite direction

    # Update state
    updated_state = {
        'current_coordinates': new_coords,
        'current_direction': new_direction,
        'current_street': target_street[2]['name'],
        'forward': forward,
        'next_point': next_point
    }

    return updated_state

# Usage example:
initial_state = {
    'current_coordinates': (0, 0),
    'current_direction': 0,
    'current_street': None
}
test_results = [
    {"actions": ["Head", "continue"], "directions": ["northeast"], "start_streets": ["Hintere"], "end_streets": [], "distances": [20], "durations": [126.9]}
]
# Load graph G here using osmnx as per the local environment and use
corrected_state = correct_position(initial_state, test_results, G)
print(corrected_state)

In [ ]:
# Utility function to get the name of the current street
def get_street_name(lat, lon):
    # Create point coordinates
    point = (lat, lon)
    # Get the street network near the point
    G = ox.graph_from_point(point, dist=100, dist_type='bbox', network_type='drive')
    # Get the nearest street edge
    nearest_edge = ox.distance.nearest_edges(G, lon, lat)  # May return a single edge or multiple edges

    # Handle the type returned by nearest_edge to ensure it is a list of edges
    if isinstance(nearest_edge, tuple):
        edges = [nearest_edge]  # If it's a single tuple, convert it to a list
    elif isinstance(nearest_edge, int):
        edges = [(nearest_edge, nearest_edge, 0)]  # Create a list containing a single edge
    else:
        edges = nearest_edge  # If it's already a list, use it directly

    # Get street names
    street_names = []
    for u, v, key in edges:
        info = G.get_edge_data(u, v, key)
        street_names.append(info.get('name', 'Unnamed Street'))  # If there is no name, return 'Unnamed Street'

    return street_names

# Usage example
lat, lon = 49.4037921, 8.6231544  # A coordinate point
street_names = get_street_name(lat, lon)
print(street_names)

In [ ]:
def generate_answer(route, working_folder_path):
    """Generate a path along the network for a list of latitude-longitude points, visualize and save it as GeoJSON."""
    # Load the graph around the first point with enough margin
    print("Received a route", route)
    G = ox.graph_from_point(route[0], dist=1000, network_type='walk', simplify=True)

    # Plot the graph
    fig, ax = ox.plot_graph(G, show=False, close=False)

    # Directly plot given points as they are on the road
    for index, (lat, lon) in enumerate(route):
        ax.scatter(lon, lat, c='green', s=10, zorder=5)  # Green dot for the route node
        ax.text(lon, lat, str(index), fontsize=12, ha='right', color='green')

    # Connect points with the shortest path
    full_route = []
    route_nodes = [ox.nearest_nodes(G, lon, lat) for lat, lon in route]
    for i in range(len(route_nodes) - 1):
        part_route = nx.shortest_path(G, route_nodes[i], route_nodes[i+1], weight='length')
        full_route.extend(part_route[:-1])  # extend to avoid duplicating nodes
    full_route.append(route_nodes[-1])  # add the last node
    
    # Plot the route
    if len(full_route) > 1:
        # Draw the function, omit during runtime
        #ox.plot_graph_route(G, full_route, route_color='r', route_linewidth=6, ax=ax)
        pass
    else:
        print("Warning: Route is too short to plot.")

    # Adjust the view to show only the route's central area
    center_x, center_y = route[0][1], route[0][0]
    ax.set_xlim([center_x - 0.0003, center_x + 0.0003])
    ax.set_ylim([center_y - 0.0003, center_y + 0.0003])

    # Convert the full route to a LineString and save as GeoJSON
    # Print(full_route)
    gdf = ox.routing.route_to_gdf(G, full_route, weight='length')

    # Because there could be list in "osmid" and "highway" columns, we need to drop them
    if 'osmid' in gdf.columns:
        gdf = gdf.drop("osmid", axis=1)
        
    if 'highway' in gdf.columns:
        gdf = gdf.drop("highway", axis=1)

    if 'maxspeed' in gdf.columns:
        gdf = gdf.drop("maxspeed", axis=1)

    if 'reversed' in gdf.columns:
        gdf = gdf.drop("reversed", axis=1)
    
    #print("Working folder path:", working_folder_path)
    output_file_path = os.path.join(working_folder_path, 'answer_newway.geojson')


    try:
        # Your code
        gdf.to_file(output_file_path, driver='GeoJSON')
    except Exception as e:
        # Catch the exception and print detailed error information
        print("An error occurred:")
        traceback.print_exc()
        
        # Print the gdf variable
        print("Current gdf variable:")
        print(gdf)


    #plt.show()

    return full_route
    
#generate_answer(route)

# Local test
# route = [(49.3896817, 8.6874513),
#  (49.3896817, 8.6874513),
#  (49.3904212, 8.6873788),
#  (49.3904771, 8.6873829),
#  (49.3907884, 8.6873535),
#  (49.390852300000006, 8.6873455),
#  (49.39107659999999, 8.6873172),
#  (49.3914058, 8.6872757),
#  (49.39165599999998, 8.6872512),
#  (49.39186809999999, 8.6872308),
#  (49.3922962, 8.6871896),
#  (49.39261809999999, 8.6871606),
#  (49.3928334, 8.6871408),
#  (49.39285299999999, 8.6871382),
#  (49.39354291656521, 8.686336300964667),
#  (49.39354291656521, 8.686336300964667),
#  (49.39353630829411, 8.686019450654992),
#  (49.39353630829411, 8.686019450654992),
#  (49.393654600000005, 8.6860084),
#  (49.393654600000005, 8.6860084),
#  (49.393646399999994, 8.6858076),
#  (49.393635399999994, 8.6856821),
#  (49.39363074049653, 8.685547073517766),
#  (49.39363074049653, 8.685547073517766),
#  (49.393795299999994, 8.685519),
#  (49.39505979999999, 8.685486),
#  (49.3966848, 8.68533),
#  (49.3966848, 8.68533),
#  (49.396752137312426, 8.685249394743417),
#  (49.39714326088968, 8.685219233267041)]

# generate_answer(route, 'data_set/0')


In [ ]:
import json
from shapely.geometry import LineString
from shapely.ops import linemerge
import shapely.geometry

def merge_line_features(geojson_data):
    # Parse the processed GeoJSON data
    features = geojson_data['features']
    
    # Extract all line segments
    lines = [LineString(feature['geometry']['coordinates']) for feature in features]
    
    # Merge the line segments
    merged_line = linemerge(lines)
    
    # Create the merged feature
    merged_feature = {
        "type": "Feature",
        "properties": {},  # You can add retained properties here if needed
        "geometry": shapely.geometry.mapping(merged_line)  # Convert Shapely Geometry object to GeoJSON format
    }
    
    # Create the new GeoJSON object
    new_geojson = {
        "type": "FeatureCollection",
        "crs": geojson_data['crs'],
        "features": [merged_feature]
    }
    
    return new_geojson

def read_geojson(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        return json.load(file)

def save_geojson(data, file_path):
    with open(file_path, 'w', encoding='utf-8') as file:
        json.dump(data, file, indent=2)

# # Specify the input and output file paths
# input_file_path = 'answer_newway.geojson'  # Replace with your input file path
# output_file_path = 'answer_combin.geojson'  # Replace with your output file path

# # Read the GeoJSON data
# geojson_data = read_geojson(input_file_path)

# # Process and merge GeoJSON features
# merged_geojson = merge_line_features(geojson_data)

# # Save the new GeoJSON data to file
# save_geojson(merged_geojson, output_file_path)

# print("GeoJSON data has been processed and saved to:", output_file_path)


In [ ]:
import requests
import json

url = "http://XX.XX.X.XX/similarity"

payload = json.dumps({
  "data": {
    "format": "geojson",
    "encoding": "plain_text",
    "content": "{\"type\": \"FeatureCollection\", \"features\": [{\"type\": \"Feature\", \"geometry\": {\"type\": \"LineString\", \"coordinates\": [[11.53041, 48.18207], [11.5304, 48.18209], [11.53214, 48.18218], [11.53243, 48.18221], [11.53335, 48.18237], [11.53443, 48.18259], [11.53539, 48.18282], [11.53688, 48.18337], [11.53769, 48.1837], [11.53932, 48.18443], [11.53953, 48.18453], [11.54109, 48.18547], [11.54154, 48.18575], [11.5417, 48.18583], [11.54193, 48.18591], [11.54215, 48.18595], [11.54252, 48.18597], [11.54656, 48.18599], [11.54742, 48.186], [11.54904, 48.18595], [11.54998, 48.18591], [11.55019, 48.18589], [11.55063, 48.18579], [11.55117, 48.18563], [11.55173, 48.18531], [11.55204, 48.18507], [11.55351, 48.18304], [11.55515, 48.18062], [11.55598, 48.17937], [11.55578, 48.17931]]}}, {\"type\": \"Feature\", \"geometry\": {\"type\": \"LineString\", \"coordinates\": [[11.53029, 48.18207], [11.53041, 48.18207], [11.53041, 48.18206], [11.53041, 48.18206], [11.53332, 48.18215], [11.53367, 48.18217], [11.53398, 48.18222], [11.53562, 48.18251], [11.5359, 48.18258], [11.53622, 48.18267], [11.5365, 48.18277], [11.5368, 48.18291], [11.54113, 48.1854], [11.54135, 48.18552], [11.54161, 48.18563], [11.54183, 48.18572], [11.54205, 48.18579], [11.54229, 48.18585], [11.54259, 48.18591], [11.54282, 48.18595], [11.54309, 48.18597], [11.54339, 48.18598], [11.54382, 48.18599], [11.54616, 48.18598], [11.54764, 48.18595], [11.54764, 48.18595], [11.54764, 48.18595], [11.54872, 48.18592], [11.54899, 48.18589], [11.54937, 48.18584], [11.54976, 48.18577], [11.55011, 48.18568], [11.55045, 48.18559], [11.55073, 48.18547], [11.55109, 48.1853], [11.55162, 48.18501], [11.55207, 48.18471], [11.55233, 48.18449], [11.55257, 48.18427], [11.55279, 48.184], [11.55299, 48.18373], [11.55312, 48.18351], [11.55329, 48.18316], [11.55347, 48.18282], [11.5544, 48.18139], [11.55522, 48.18002], [11.55531, 48.17988], [11.55571, 48.17928], [11.55578, 48.17931], [11.55578, 48.17922]]}}]}"
  },
  "weights": {
    "angle": 0, # Angle between the line connecting the start and end points
    "edr": 0,  # Edit distance (not very important)
    "endpoints_shift": 0, # Sum of the offsets of the start and end points
    "hausdorff": 0, # 
    "iou": 0, # Buffer
    "length_ratio": 0 # Length difference
  },
  "thresholds": {
    "nearest_junction_meters": 100, # Search range
    "confidence_percentage": 0
  }
})
headers = {
  'Content-Type': 'application/json'
}

response = requests.request("POST", url, headers=headers, data=payload)

print(response.text)

In [3]:
def load_geojson(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        return json.load(file)

def process_geojson(n=None):
    data_set_path = 'data_set'
    subfolders = []

    # Determine whether to process a single folder or all folders
    if n is not None:
        folder_path = os.path.join(data_set_path, str(n))
        if os.path.isdir(folder_path):
            subfolders.append(str(n))
        else:
            print(f"Folder {n} does not exist in {data_set_path}.")
            return
    else:
        # Get all subfolders in data_set and sort them numerically
        subfolders = sorted([f for f in os.listdir(data_set_path) if os.path.isdir(os.path.join(data_set_path, f))], key=int)

    # Initialize counters and data structures
    total_tests = 0
    success_count = 0
    failure_count = 0
    requests_failure_count = 0
    success_folders = []
    failure_folders = []

    # Process each subfolder
    for subfolder in subfolders:
        total_tests += 1
        folder_path = os.path.join(data_set_path, subfolder)
        answer_combin_path = os.path.join(folder_path, 'answer_combin.geojson')
        answer_compare_path = os.path.join(folder_path, 'route.geojson')

        # Check if necessary files exist
        if not os.path.exists(answer_combin_path) or not os.path.exists(answer_compare_path):
            print(f"Missing necessary GeoJSON files in folder {subfolder}, skipping this folder.")
            failure_count += 1
            failure_folders.append(subfolder)
            continue

        # Load GeoJSON files
        try:
            geojson1 = load_geojson(answer_combin_path)
            geojson2 = load_geojson(answer_compare_path)
            
        except Exception as e:
            print(f"Error loading GeoJSON files in folder {subfolder}: {e}")
            failure_count += 1
            failure_folders.append(subfolder)
            continue

        # Merge features
        merged_features = geojson1['features'] + geojson2['features']


        # Create new GeoJSON content
        new_geojson_content = json.dumps({
            "type": "FeatureCollection",
            "features": merged_features
        })

        print(new_geojson_content)

        # Build the payload for the request
        url = "http://10.221.116.140/planet/river/api/similarity"
        payload = {
            "data": {
                "format": "geojson",
                "encoding": "plain_text",
                "content": new_geojson_content
            },
            "weights": {
                "angle": 0.03,
                "edr": 0.05,
                "endpoints_shift": 0.05,
                "hausdorff": 0.4,
                "iou": 0.17,
                "length_ratio": 0.30
            },
            "thresholds": {
                "nearest_junction_meters": 2000,
                "confidence_percentage": 0.6
            }
        }
        headers = {
            'Content-Type': 'application/json'
        }

        # Send the request and process the response
        try:
            response = requests.post(url, headers=headers, data=json.dumps(payload))
            response.raise_for_status()
            response_data = response.json()

            print(response_data)

            # Check the 'is_match' field in the response
            if response_data.get('is_match'):
                print(f"Folder {subfolder}: Match successful")
                success_count += 1
                success_folders.append(subfolder)
            else:
                print(f"Folder {subfolder}: Match failed")
                failure_count += 1
                failure_folders.append(subfolder)

            # Save the response to a file (optional)
            with open(os.path.join(folder_path, 'response.json'), 'w', encoding='utf-8') as f:
                json.dump(response_data, f, ensure_ascii=False, indent=4)
        except requests.exceptions.RequestException as e:
            print(f"Request failed for folder {subfolder}: {e}")
            failure_count += 1
            requests_failure_count += 1
            failure_folders.append(subfolder)
        except json.JSONDecodeError as e:
            print(f"Error parsing JSON response for folder {subfolder}: {e}")
            failure_count += 1
            failure_folders.append(subfolder)

    # Calculate success rate
    if total_tests > 0:
        success_rate = success_count / (total_tests - requests_failure_count)
        print("\n===== Test Results =====")
        print(f"Total tests: {total_tests}")
        print(f"Successful matches: {success_count}")
        print(f"Failed matches: {failure_count}")
        print(f"Success rate: {success_rate:.2%}")
        print(f"Folders with successful matches: {success_folders}")
        print(f"Folders with failed matches: {failure_folders}")
    else:
        print("No test cases found to process.")

# Example usage:
# Process folder number 3
# process_geojson(3)

# Process all folders
process_geojson()

{"type": "FeatureCollection", "features": [{"type": "Feature", "properties": {}, "geometry": {"type": "LineString", "coordinates": [[-79.4169298, 43.6799165], [-79.4172186, 43.6806578], [-79.4174145, 43.6811422], [-79.4174479, 43.6812255], [-79.4175841, 43.6815628], [-79.4176233, 43.6816599], [-79.417689, 43.681834], [-79.4176876, 43.6818459], [-79.4176815, 43.6818606], [-79.4177063, 43.6819213], [-79.4177333, 43.6819877], [-79.4177532, 43.6820099], [-79.4177787, 43.6820538], [-79.4179141, 43.6824101], [-79.4181114, 43.6830275], [-79.4180986, 43.6830458], [-79.4182143, 43.683023], [-79.4182284, 43.6830203], [-79.4182314, 43.6830197], [-79.4183654, 43.6829934], [-79.4196808, 43.6827409], [-79.4197412, 43.6827117], [-79.4198771, 43.6826821], [-79.4199226, 43.6826722], [-79.4199466, 43.6826668], [-79.4200349, 43.6826478], [-79.420363, 43.6825905], [-79.4203835, 43.6826458], [-79.4204024, 43.682697], [-79.4204083, 43.682713], [-79.4204127, 43.682725], [-79.4204335, 43.6827811], [-79.420449

In [ ]:
from openai import OpenAI
client = OpenAI(api_key='')

response = client.images.generate(
    prompt="A cute baby sea otter",
    n=2,
    size="1024x1024"
)

print(response.data[0].url)

In [4]:
# Module to get the latitude and longitude of the start and end points of the corresponding route
# Used to provide additional information for instructions in the project
def get_start_end_points(folder_name):
    data_set_dir = "data_set"
    folder_path = os.path.join(data_set_dir, folder_name)
    geojson_file_path = os.path.join(folder_path, "route.geojson")

    # Check if the file exists
    if os.path.isfile(geojson_file_path):
        with open(geojson_file_path, 'r', encoding='utf-8') as file:
            geojson_data = json.load(file)
            
            # Extract start and end coordinates from metadata
            coordinates = geojson_data.get('metadata', {}).get('query', {}).get('coordinates', [])
            if coordinates and len(coordinates) >= 2:
                start_point = coordinates[0]
                end_point = coordinates[1]
                # Return the labeled coordinates
                return {'start': f"start point：{start_point}", 'end': f"end point：{end_point}"}
    return {'start': None, 'end': None}

# Suppose you are processing the folder named '0'
start_end_point = get_start_end_points('0')
print(start_end_point)

{'start': 'start point：[-79.3505371, 43.7162514]', 'end': 'end point：[-79.3564007, 43.7147569]'}


In [15]:
def get_natural_language_instructions(folder_name=None):
    data_set_dir = "data_set"
    
    # Custom sort function to sort folders numerically
    def numeric_sort(folder_name):
        # Extract the numeric part of the folder name for sorting
        numbers = re.findall(r'\d+', folder_name)
        return [int(num) for num in numbers] if numbers else [folder_name]

    # List to store the final results
    result_list = []

    # If no folder name is provided, read files from all subfolders
    if folder_name is None:
        # Use the custom numeric_sort() to ensure folders are read in numeric order
        folder_names = [folder for folder in os.listdir(data_set_dir) if os.path.isdir(os.path.join(data_set_dir, folder))]
        folder_names_sorted = sorted(folder_names, key=numeric_sort)

        # Iterate through all folders and process each one in order
        for folder in folder_names_sorted:
            folder_path = os.path.join(data_set_dir, folder)

            # Read the natural language instructions file
            instructions_file_path = os.path.join(folder_path, "natural_instructions.txt")
            if os.path.isdir(folder_path) and os.path.isfile(instructions_file_path):
                with open(instructions_file_path, 'r', encoding='utf-8') as file:
                    instructions_data = file.read()  # or use readlines()
                
                # Get the start and end coordinates
                start_end_points = get_start_end_points(folder)

                # Merge coordinates and instructions
                if start_end_points['start'] and start_end_points['end']:
                    merged_data = f"{start_end_points['start']} {start_end_points['end']}\n{instructions_data}"
                    result_list.append(merged_data)

        return result_list
    
    # If a folder name is provided, only read files from the specified folder
    else:
        folder_path = os.path.join(data_set_dir, folder_name)
        instructions_file_path = os.path.join(folder_path, "natural_instructions.txt")
        
        # Check if the file exists
        if os.path.isfile(instructions_file_path):
            with open(instructions_file_path, 'r', encoding='utf-8') as file:
                instructions_data = file.read()  # or use readlines()
            
            # Get the start and end coordinates
            start_end_points = get_start_end_points(folder_name)

            # Merge coordinates and instructions
            if start_end_points['start'] and start_end_points['end']:
                merged_data = f"{start_end_points['start']} {start_end_points['end']}\n{instructions_data}"
                return merged_data
        else:
            print(f"File {instructions_file_path} does not exist.")
            return None
# Test function

# Read data from all folders and ensure numeric order
# result_all_folders = get_natural_language_instructions()
# print(result_all_folders)

# Read data from a specified folder
result_single_folder = get_natural_language_instructions()
print(result_single_folder[4])

results_API_upload = []

for text in result_single_folder:
    lines = text.split('\n')
    processed_lines = [lines[0]]  # Keep the first line

    for line in lines[1:]:
        # Remove "and taking about xxx seconds."
        line = re.sub(r' and taking about [\d\.]+ seconds\.', '.', line)
        # Add a period after "meters" if not already present
        line = re.sub(r'(meters)(?!\.)', r'\1.', line)
        processed_lines.append(line)

    processed_text = '\n'.join(processed_lines)
    results_API_upload.append(processed_text)

print(len(results_API_upload))
print(results_API_upload[4])

start point：[-79.4332579, 43.6465301] end point：[-79.4365366, 43.6521124]
Head west, continue for 75.9 meters and taking about 54.6 seconds.
Turn slight right, continue for 37.7 meters and taking about 27.1 seconds.
Turn left, continue for 11.3 meters and taking about 8.1 seconds.
Turn right, continue for 126.3 meters and taking about 90.9 seconds.
Keep right, continue for 91.7 meters and taking about 66.0 seconds.
Keep right, continue for 146.6 meters and taking about 105.5 seconds.
Turn slight left, continue for 2.3 meters and taking about 1.6 seconds.
Turn right, continue for 18.8 meters and taking about 13.6 seconds.
Turn right, continue for 198.7 meters and taking about 143.1 seconds.
Turn left, continue for 4.8 meters and taking about 3.5 seconds.
Turn right, continue for 18.7 meters and taking about 13.5 seconds.
Turn right, continue for 2.1 meters and taking about 1.5 seconds.
Keep left, continue for 26.4 meters and taking about 19.0 seconds.
Arrive at your destination, straigh

In [ ]:
import openai

# Set API key (please replace 'YOUR_API_KEY' with your actual API key)
#openai.api_key = 'YOUR_API_KEY'
client = OpenAI(api_key="")
# Define model name
MODEL = "gpt-4o"  # If you don't have access to GPT-4, you can use "gpt-3.5-turbo"

# Define the initial prompt to establish the game rules and scenario
prompt = """
You're in Toronto, Canada. Please generate a road network for that city in your mind based on your knowledge.
Each of the next sets of navigation commands describes the walk from S to D. Describe going from D to S in the same style, following these rules.
1. the first step must give the absolute direction (e.g. East, West, North, South.....). You can't use instructions like "Start at your destination heading straight backward", if have to be absoulute clear.
2. you cannot simply use inversion semantics; you have to understand the route itself.
3. The format of the reverse navigation instruction can be found in the input instruction. Use 'head' 'turn' 'continue' 'arrive' for the key movement.
4. Tell me your cofidence about the reverse results in the end by percentage (e.g. 50% when you are not sure, 90% when you are very sure) and explain a bit why you choose this confidence on each route query.
5. The number of output instructions is supposed to be the same as the input.
6. Try to tell me some POI or any landmarks exist close to the route if you really understand route in GIS sense.
7. The first step must be absolute direction, this is the most importatn part, you can not violate this rule.

Example form:
Head northwest on Wychwood Avenue on Wychwood Avenue, continue for 3.3 meters.
Turn left, continue for 6.1 meters.
Keep left, continue for 24.8 meters.
Turn right, continue for 113.3 meters.
Turn left, continue for 139.6 meters.
Turn right, continue for 67.3 meters.
Turn sharp left, continue for 7.3 meters.
Turn right onto Tyrrel Avenue on Tyrrel Avenue, continue for 189.2 meters.
Turn left onto Turner Road on Turner Road, continue for 89.7 meters.
Turn right onto Bracondale Hill Road on Bracondale Hill Road, continue for 85.6 meters.
Turn left onto Frank Crescent on Frank Crescent, continue for 7.0 meters.
Turn right, continue for 181.6 meters.
Turn right, continue for 2.1 meters.
Arrive at your destination, straight ahead, continue for 0.0 meters.

"""


# Create the initial message list, including the user's initial prompt
messages = [
    {"role": "user", "content": prompt}
]

# Initialize the list to store assistant replies
natural_languages_instructions = results_API_upload
# This is used to control whether to send all at once
#natural_languages_instructions = results_API_upload


natural_languages_api_results = []

# # Define your navigation instruction list
# natural_languages_instructions = [
#     """
#     Head east, continue for 96.1 meters and taking about 69.2 seconds.
#     Turn right onto Don Trail on Don Trail, continue for 54.1 meters and taking about 39.0 seconds.
#     Turn sharp right, continue for 31.2 meters and taking about 22.5 seconds.
#     Turn slight right onto Swamp on Swamp, continue for 31.1 meters and taking about 22.4 seconds.
#     Keep right onto Swamp on Swamp, continue for 141.7 meters and taking about 102.0 seconds.
#     Turn left onto Vanderhoof Hill on Vanderhoof Hill, continue for 179.2 meters and taking about 129.1 seconds.
#     Turn right onto Vanderhoof Avenue on Vanderhoof Avenue, continue for 99.3 meters and taking about 71.5 seconds.
#     Turn right onto Glassworks Drive on Glassworks Drive, continue for 7.9 meters and taking about 5.7 seconds.
#     Turn left, continue for 76.7 meters and taking about 55.3 seconds.
#     Turn right onto Brian Peck Crescent on Brian Peck Crescent, continue for 46.0 meters and taking about 33.1 seconds.
#     Turn left onto Brian Peck Crescent on Brian Peck Crescent, continue for 65.2 meters and taking about 47.0 seconds.
#     Turn right, continue for 114.9 meters and taking about 82.8 seconds.
#     Turn right, continue for 6.3 meters and taking about 4.5 seconds.
#     Arrive at your destination, straight ahead, continue for 0.0 meters and taking about 0.0 seconds.
#     """,
#     """
#     Head east, continue for 11.8 meters and taking about 8.5 seconds.
#     Turn left, continue for 42.7 meters and taking about 30.8 seconds.
#     Turn slight left, continue for 29.2 meters and taking about 21.0 seconds.
#     Turn left, continue for 47.6 meters and taking about 34.3 seconds.
#     Turn right, continue for 38.1 meters and taking about 27.4 seconds.
#     Turn right, continue for 16.0 meters and taking about 11.5 seconds.
#     Turn right, continue for 56.4 meters and taking about 40.6 seconds.
#     Turn right, continue for 462.0 meters and taking about 332.6 seconds.
#     Turn left, continue for 14.2 meters and taking about 10.2 seconds.
#     Keep right, continue for 19.5 meters and taking about 14.0 seconds.
#     Turn right, continue for 93.9 meters and taking about 67.6 seconds.
#     Turn left onto Humber River Trail on Humber River Trail, continue for 230.3 meters and taking about 165.8 seconds.
#     Turn sharp left, continue for 55.4 meters and taking about 39.9 seconds.
#     Turn sharp right, continue for 17.2 meters and taking about 12.4 seconds.
#     Keep right, continue for 212.2 meters and taking about 152.8 seconds.
#     Turn left, continue for 77.1 meters and taking about 55.5 seconds.
#     Arrive at your destination, straight ahead, continue for 0.0 meters and taking about 0.0 seconds.
#     """
# ]

start_idx = 763  # Start from folder number 763

# Iterate through the navigation instruction list, send and get replies one by one
for idx, instruction in enumerate(natural_languages_instructions[start_idx:], start=start_idx):
    # Add the current navigation instruction as a user message to the message list
    messages.append({"role": "user", "content": instruction})
    
    # Call the OpenAI API, send the current message list
    completion = client.chat.completions.create(
        model=MODEL,
        messages=messages,
        #temperature= 0.1
    )
    
    # Get the assistant's reply
    assistant_reply = completion.choices[0].message.content
    
    # Add the assistant's reply to the result list
    natural_languages_api_results.append(assistant_reply)
    
    # To maintain context, also add the assistant's reply to the message list
    messages.append({"role": "assistant", "content": assistant_reply})

    # Get the corresponding folder path
    folder_path = os.path.join('data_set', str(idx))
    
    # If the folder does not exist, create it
    if not os.path.exists(folder_path):
        os.makedirs(folder_path)
    
    # Define the file path
    file_path = os.path.join(folder_path, 'reverse_route.txt')
    
    # Write the assistant's reply to the reverse_route.txt file
    with open(file_path, 'w') as file:
        file.write(assistant_reply)


# Output all assistant replies
for idx, reply in enumerate(natural_languages_api_results):
    print(f"Reply for instruction set {idx + 1}:")
    print(reply)
    print("\n")


In [1]:
from openai import OpenAI
client = OpenAI()


prompt = """
You're in Toronto, Canada. Please generate a road network for that city in your mind based on your knowledge.
Each of the next sets of navigation commands describes the walk from S to D. Describe going from D to S in the same style, following these rules.
1. the first step must give the absolute direction (e.g. East, West, North, South.....). You can't use instructions like "Start at your destination heading straight backward", if have to be absoulute clear.
2. you cannot simply use inversion semantics; you have to understand the route itself.
3. The format of the reverse navigation instruction can be found in the input instruction. Use 'head' 'turn' 'continue' 'arrive' for the key movement.
4. Tell me your cofidence about the reverse results in the end by percentage (e.g. 50% when you are not sure, 90% when you are very sure) and explain a bit why you choose this confidence on each route query.
5. The number of output instructions is supposed to be the same as the input.
6. Try to tell me some POI or any landmarks exist close to the route if you really understand route in GIS sense.
7. The first step must be absolute direction, this is the most importatn part, you can not violate this rule.

Example form:
Head northwest on Wychwood Avenue on Wychwood Avenue, continue for 3.3 meters.
Turn left, continue for 6.1 meters.
Keep left, continue for 24.8 meters.
Turn right, continue for 113.3 meters.
Turn left, continue for 139.6 meters.
Turn right, continue for 67.3 meters.
Turn sharp left, continue for 7.3 meters.
Turn right onto Tyrrel Avenue on Tyrrel Avenue, continue for 189.2 meters.
Turn left onto Turner Road on Turner Road, continue for 89.7 meters.
Turn right onto Bracondale Hill Road on Bracondale Hill Road, continue for 85.6 meters.
Turn left onto Frank Crescent on Frank Crescent, continue for 7.0 meters.
Turn right, continue for 181.6 meters.
Turn right, continue for 2.1 meters.
Arrive at your destination, straight ahead, continue for 0.0 meters.

"""

completion = client.chat.completions.create(
  model="gpt-4o",
  messages=[
    {"role": "user", "content": prompt}
  ],
  logprobs=True,
  top_logprobs=2
)

print(completion.choices[0].message)
print(completion.choices[0].logprobs)


ChatCompletionMessage(content='Head south on Bracondale Hill Road, continue for 85.6 meters.\nTurn left onto Turner Road, continue for 89.7 meters.\nTurn right onto Tyrrel Avenue, continue for 189.2 meters.\nTurn sharp right, continue for 7.3 meters.\nTurn left, continue for 67.3 meters.\nTurn right, continue for 139.6 meters.\nTurn left, continue for 113.3 meters.\nKeep right, continue for 24.8 meters.\nTurn right, continue for 6.1 meters.\nHead southeast on Wychwood Avenue, continue for 3.3 meters.\nArrive at your starting location, straight ahead, continue for 0.0 meters.\n\nConfidence: 80%\n\nExplanation: The road network in Toronto is quite grid-like in many residential neighborhoods, and the instructions provided seem to correspond to a typical pathway one might encounter. However, certain segments like "Turn sharp left" or "keep left" might be less intuitive in reverse without a map to verify. My understanding of the grid layout in Toronto boosts confidence, but nuanced or uniqu